## 更新事項
>2021.1.18
 * 修正一次可切不同顆sensor
 * mapping figure檔名增加timestamp
 
## 主要功能
* 4R_7341 sensor data select
* Moving average
* MFC#1 ppm conversion
* Three type select data function
  1. select_data_A, plot_data_A
     - selected_range = { select: end}, default datapoint = 50
  2. select_data_B, plot_data_B
     - selected_range = { select: (start, end)}
  3. select_data_C, plot_data_C
     - selected_range = { select: (end, datapoint)}
* develope CIEx,y and Lab convert
* save mapping figure

In [74]:
import os
import pandas as pd
import numpy as np
import save_mapping_figure 
from remove_spike import remove_spike

import plotly.graph_objects as go
# import plotly.offline as offline
# import cufflinks as cf
from plotly.offline import init_notebook_mode, iplot
# cf.go_offline(connected=True)

import warnings
warnings.filterwarnings('ignore')

import json

from select_data_7341 import select_data_7341

# import tkinter
from tkinter import*
# Create Tk root
root = Tk()
# Hide the main window
root.withdraw()
root.call('wm', 'attributes', '.', '-topmost', True)
from tkinter import filedialog
%gui tk

In [75]:
def path_loading():
    path = filedialog.askopenfilename(filetypes = (("Comma-Separated Values","*.csv"),("All Files","*.*")),multiple=True)
    print(path)
    return path

In [76]:
def split(path_list):
    j=0
    x = []
    while j < len(path_list):
        x.append(path_list[j].split('_')[-2])
        j+=1
    return x

In [77]:
# def remove_spike(data):
#     AMS1_spike_index = data[abs(data['583nm #1']-data['583nm #1'][0:10].mean())>2000].index
#     AMS2_spike_index = data[abs(data['583nm #2']-data['583nm #2'][0:10].mean())>2000].index
#     print('AMS1_spike_index', AMS1_spike_index)
#     print('AMS2_spike_index', AMS2_spike_index)
#     spike_index = np.append(AMS1_spike_index, AMS2_spike_index)
#     data.drop(labels=spike_index, inplace=True)
#     return data

In [78]:
# def auto_select(data):
     
#     dict_set=[]

#     for index in range(data.shape[0]):
        
#         #  取calibration 0ppm
#         if index < 690:
#             flag = 0
#             dict_number = 0 
            
#             i = data['MFC#3'][index]
#             dict_number = dict_number +1
            
#             if flag == 0:
#                 if i > 2.9 and i <3.1:
#                     dict_set.append(dict_number-2)
#                     flag = 1
            
#             elif flag == 1 and i < 1:
#                 flag = 0
                    
#         # 取calibration 濃度值    
#         else:
#             flag = False
#             dict_number = 0 
            
#             i = data['MFC#1'][index]
#             dict_number = dict_number + 1
#             if flag == False:
#                 if i>0.9 and i<1.1:
#                     dict_set.append(dict_number-2)    
#                     flag=True

#                 elif i>9.9 and i<10.1:
#                     dict_set.append(dict_number-2)    
#                     flag=True

#                 elif i>6.15 and i<6.35:
#                     dict_set.append(dict_number-2)
#                     flag=True

#                 elif i>15:
#                     dict_set.append(dict_number-2)
#                     flag=True

#             elif flag ==True:
#                 if i == 0.0:
#                     dict_set.append(dict_number-2)
#                     flag=False

# #             elif flag == 10:
# #                 if i<1.0:
# #                     dict_set.append(dict_number-2)
# #                     flag=0

# #             elif flag == 25:
# #                 if i<1.0:
# #                     dict_set.append(dict_number-2)
# #                     flag=0

# #             elif flag == 60:
# #                 if i<1.0:
# #                     dict_set.append(dict_number-2)
# #                     flag=0

#     return dict_set

In [79]:
def auto_select(data):
    flag = 0
    dict_number = 0  
    dict_set=[]

    for i in data['MFC#1']:   
        dict_number = dict_number + 1

        if flag == 0:
            if i>0.95 and i<1.05:
                dict_set.append(dict_number-3)    
                flag=4

            elif i>2.45 and i<2.55:
                dict_set.append(dict_number-3)    
                flag=10

            elif i>6.2 and i<6.3:
                dict_set.append(dict_number-3)
                flag=25
                
            elif i>14.5 and i<15.5:
                dict_set.append(dict_number-3)
                flag=60

        elif flag == 4:
            if i<0.5:
                dict_set.append(dict_number-3)
                flag=0

        elif flag == 10:
            if i<0.5:
                dict_set.append(dict_number-3)
                flag=0

        elif flag == 25:
            if i<0.5:
                dict_set.append(dict_number-3)
                flag=0
                
        elif flag == 60:
            if i<0.5:
                dict_set.append(dict_number-3)
                flag=0
                
    return dict_set

In [80]:
path_list = path_loading()

('C:/Users/bioinspira/Desktop/store at 30C/2021_04_14_13_38_50_round2/dual7341_#20200814093320_202104141338.csv', 'C:/Users/bioinspira/Desktop/store at 30C/2021_04_14_13_38_50_round2/dual7341_#20200814093632_202104141338.csv', 'C:/Users/bioinspira/Desktop/store at 30C/2021_04_14_13_38_50_round2/dual7341_#20200817093518_202104141338.csv', 'C:/Users/bioinspira/Desktop/store at 30C/2021_04_14_13_38_50_round2/dual7341_#20200819094714_202104141338.csv', 'C:/Users/bioinspira/Desktop/store at 30C/2021_04_14_13_38_50_round2/dual7341_#20200915135041_202104141338.csv', 'C:/Users/bioinspira/Desktop/store at 30C/2021_04_14_13_38_50_round2/dual7341_#20200917104028_202104141338.csv', 'C:/Users/bioinspira/Desktop/store at 30C/2021_04_14_13_38_50_round2/dual7341_#20200917104408_202104141338.csv', 'C:/Users/bioinspira/Desktop/store at 30C/2021_04_14_13_38_50_round2/dual7341_#20200918095055_202104141338.csv')


### select_data_C (selected_range format)
- selected_range = { select: (end, datapoint)}

## Parameter setting

In [81]:
'''chamber 1 NH3 cylinder concentration 1800ppm
   chamber 4 NH3 cylinder concentration 1000ppm'''

MFC1_max_flow_rate = 0.8
total_flow_rate = 2
cylinder_concentration = 1000
# sensor_channels = ['Sub Concentration']
sensor_channels = ['583nm #1']

In [82]:
# selected_range_10 = {   
#              '10C 60% 0ppm': (dict_set[0], 10),
#              '10C 60% 4ppm': (dict_set[1], 10),
#              '10C 60% 10ppm': (dict_set[3], 10),
#              '10C 60% 30ppm': (dict_set[5], 10),

#              '10C 70% 0ppm': (dict_set[6], 10),
#              '10C 70% 4ppm': (dict_set[7], 10),
#              '10C 70% 10ppm': (dict_set[9], 10),
#              '10C 70% 30ppm': (dict_set[11], 10),

#              '10C 85% 0ppm': (dict_set[12], 10),
#              '10C 85% 10ppm': (dict_set[13], 10),
#              '10C 85% 30ppm': (dict_set[15], 10),
#              '10C 85% 60ppm': (dict_set[17], 10),                  
#               } 
    
# selected_range_20 = {   
#          '20C 60% 0ppm': (dict_set[18], 10),
#          '20C 60% 4ppm': (dict_set[19], 10),
#          '20C 60% 10ppm': (dict_set[21], 10),
#          '20C 60% 30ppm': (dict_set[23], 10),

#          '20C 70% 0ppm': (dict_set[24], 10),
#          '20C 70% 4ppm': (dict_set[25], 10),
#          '20C 70% 10ppm': (dict_set[27], 10),
#          '20C 70% 30ppm': (dict_set[29], 10),

#          '20C 85% 0ppm': (dict_set[30], 10),
#          '20C 85% 10ppm': (dict_set[31], 10),
#          '20C 85% 30ppm': (dict_set[33], 10),
#          '20C 85% 60ppm': (dict_set[35], 10),                  
#           } 

# selected_range_30 = {   
#          '30C 60% 0ppm': (dict_set[36], 10),
#          '30C 60% 4ppm': (dict_set[37], 10),
#          '30C 60% 10ppm': (dict_set[39], 10),
#          '30C 60% 30ppm': (dict_set[41], 10),

#          '30C 70% 0ppm': (dict_set[42], 10),
#          '30C 70% 4ppm': (dict_set[43], 10),
#          '30C 70% 10ppm': (dict_set[45], 10),
#          '30C 70% 30ppm': (dict_set[47], 10),

#          '30C 85% 0ppm': (dict_set[48], 10),
#          '30C 85% 10ppm': (dict_set[49], 10),
#          '30C 85% 30ppm': (dict_set[51], 10),
#          '30C 85% 60ppm': (dict_set[53], 10),                  
#           } 

# selected_range_35 = {   
#      '35C 60% 0ppm': (dict_set[54], 10),
#      '35C 60% 4ppm': (dict_set[55], 10),
#      '35C 60% 10ppm': (dict_set[57], 10),
#      '35C 60% 30ppm': (dict_set[59], 10),

#      '35C 70% 0ppm': (dict_set[60], 10),
#      '35C 70% 4ppm': (dict_set[61], 10),
#      '35C 70% 10ppm': (dict_set[63], 10),
#      '35C 70% 30ppm': (dict_set[65], 10),

#      '35C 85% 0ppm': (dict_set[66], 10),
#      '35C 85% 10ppm': (dict_set[67], 10),
#      '35C 85% 30ppm': (dict_set[69], 10),
#      '35C 85% 60ppm': (dict_set[71], 10),                  
#       } 



In [83]:
# u+4 一個溫度一個濕度60,25,10,4,0ppm
#     selected_range_10 = {   
#              '10C 0ppm': (610, 10),
#              '10C 60ppm': (dict_set[1], 10),
#              '10C 25ppm': (dict_set[3], 10),
#              '10C 10ppm': (dict_set[5], 10),
#              '10C 4ppm': (dict_set[7], 10),
#               } 
    
#     selected_range_0 = { 
#              '0C 0ppm': (419, 10),
#              '0C 60ppm': (dict_set[9], 10),
#              '0C 25ppm': (dict_set[11], 10),
#              '0C 10ppm': (dict_set[13], 10),
#              '0C 4ppm': (dict_set[15], 10),                  
#               } 
    
#     selected_range_n10 = {   
#              'n10C 0ppm': (234, 10),
#              'n10C 60ppm': (dict_set[17], 10),
#              'n10C 25ppm': (dict_set[19], 10),
#              'n10C 10ppm': (dict_set[21], 10),
#              'n10C 4ppm': (dict_set[23], 10),                  
#               }
    
#     selected_range_n20 = {   
#              'n20C 0ppm': (46, 10),
#              'n20C 60ppm': (dict_set[25], 10),
#              'n20C 25ppm': (dict_set[27], 10),
#              'n20C 10ppm': (dict_set[29], 10),
#              'n20C 4ppm': (dict_set[31], 10),                  
#               }
    
#     selected_range_n10_blind_test = {
#              'n10Cb 0ppm': (3193, 10),
#              'n10Cb 60ppm': (dict_set[33], 10),
#              'n10Cb 25ppm': (dict_set[35], 10),
#              'n10Cb 10ppm': (dict_set[37], 10),
#              'n10Cb 4ppm': (dict_set[39], 10),                  
#              }

    # blind test dictionary
#     selected_range_n10_blind_test = {
#                  'n10Cb 0ppm': (dict_set[0], 10),
#                  'n10Cb 60ppm': (dict_set[1], 10),
#                  'n10Cb 25ppm': (dict_set[3], 10),
#                  'n10Cb 10ppm': (dict_set[5], 10),
#                  'n10Cb 4ppm': (dict_set[7], 10),                  
#                  }

In [84]:
##ZnD 三個濕度 60,25,10,4,0ppm (ppm base)
#     selected_range_n20 = {   
#                  'n20C 40% 0ppm': (dict_set[0], 10),
#                  'n20C 40% 60ppm': (dict_set[1], 10),
#                  'n20C 40% 250ppm': (dict_set[3], 10),
#                  'n20C 40% 10ppm': (dict_set[5], 10),
#                  'n20C 40% 4ppm': (dict_set[7], 10),

#                  'n20C 50% 0ppm': (dict_set[8], 10),
#                  'n20C 50% 60ppm': (dict_set[9], 10),
#                  'n20C 50% 25ppm': (dict_set[11], 10),
#                  'n20C 50% 10ppm': (dict_set[13], 10),
#                  'n20C 50% 4ppm': (dict_set[15], 10),

#                  'n20C 70% 0ppm': (dict_set[16], 10),
#                  'n20C 70% 60ppm': (dict_set[17], 10),
#                  'n20C 70% 25ppm': (dict_set[19], 10),
#                  'n20C 70% 10ppm': (dict_set[21], 10), 
#                  'n20C 70% 4ppm': (dict_set[23], 10),
#               } 

#     selected_range_n10 = {   
#              'n10C 40% 0ppm': (dict_set[24], 10),
#              'n10C 40% 60ppm': (dict_set[25], 10),
#              'n10C 40% 25ppm': (dict_set[27], 10),
#              'n10C 40% 10ppm': (dict_set[29], 10),
#              'n10C 40% 4ppm': (dict_set[31], 10),

#              'n10C 50% 0ppm': (dict_set[32], 10),
#              'n10C 50% 60ppm': (dict_set[33], 10),
#              'n10C 50% 25ppm': (dict_set[35], 10),
#              'n10C 50% 10ppm': (dict_set[37], 10),
#              'n10C 50% 4ppm': (dict_set[39], 10),

#              'n10C 70% 0ppm': (dict_set[40], 10),
#              'n10C 70% 60ppm': (dict_set[41], 10),
#              'n10C 70% 25ppm': (dict_set[43], 10),
#              'n10C 70% 10ppm': (dict_set[45], 10),
#              'n10C 70% 4ppm': (dict_set[47], 10), 
#               } 

#     selected_range_0 = {   
#          '0C 40% 0ppm': (dict_set[48], 10),
#          '0C 40% 60ppm': (dict_set[49], 10),
#          '0C 40% 25ppm': (dict_set[51], 10),
#          '0C 40% 10ppm': (dict_set[53], 10),
#          '0C 40% 4ppm': (dict_set[55], 10),

#          '0C 50% 0ppm': (dict_set[56], 10),
#          '0C 50% 60ppm': (dict_set[57], 10),
#          '0C 50% 25ppm': (dict_set[59], 10),
#          '0C 50% 10ppm': (dict_set[61], 10),
#          '0C 50% 4ppm': (dict_set[63], 10),

#          '0C 70% 0ppm': (dict_set[64], 10),
#          '0C 70% 60ppm': (dict_set[65], 10),
#          '0C 70% 25ppm': (dict_set[67], 10),
#          '0C 70% 10ppm': (dict_set[69], 10),
#          '0C 70% 4ppm': (dict_set[71], 10),
#           } 

#     selected_range_10 = {   
#              '10C 40% 0ppm': (dict_set[72], 10),
#              '10C 40% 60ppm': (dict_set[73], 10),
#              '10C 40% 25ppm': (dict_set[75], 10),
#              '10C 40% 10ppm': (dict_set[77], 10),
#              '10C 40% 4ppm': (dict_set[79], 10),

#              '10C 50% 0ppm': (dict_set[80], 10),
#              '10C 50% 60ppm': (dict_set[81], 10),
#              '10C 50% 25ppm': (dict_set[83], 10),
#              '10C 50% 10ppm': (dict_set[85], 10),
#              '10C 50% 4ppm': (dict_set[87], 10),

#              '10C 70% 0ppm': (dict_set[88], 10),
#              '10C 70% 60ppm': (dict_set[89], 10),
#              '10C 70% 25ppm': (dict_set[91], 10),
#              '10C 70% 10ppm': (dict_set[93], 10), 
#              '10C 70% 4ppm': (dict_set[95], 10),
#               } 
    
#     selected_range_n10_blind_test = {   
#              'n10Cb 40% 0ppm': (dict_set[96], 10),
#              'n10Cb 40% 60ppm': (dict_set[97], 10),
#              'n10Cb 40% 25ppm': (dict_set[99], 10),
#              'n10Cb 40% 10ppm': (dict_set[101], 10),
#              'n10Cb 40% 4ppm': (dict_set[103], 10),

#              'n10Cb 50% 0ppm': (dict_set[104], 10),
#              'n10Cb 50% 60ppm': (dict_set[105], 10),
#              'n10Cb 50% 25ppm': (dict_set[107], 10),
#              'n10Cb 50% 10ppm': (dict_set[109], 10),
#              'n10Cb 50% 4ppm': (dict_set[111], 10),

#              'n10Cb 70% 0ppm': (dict_set[112], 10),
#              'n10Cb 70% 60ppm': (dict_set[113], 10),
#              'n10Cb 70% 25ppm': (dict_set[115], 10),
#              'n10Cb 70% 10ppm': (dict_set[117], 10),
#              'n10Cb 70% 4ppm': (dict_set[119], 10), 
#               } 

## Data selection process

In [85]:
spectrum_convert = True  # convert CIExy, Lab
remove_spike_switch = True
threshold = 5000         # remove spike
sensor_list = split(path_list)

# plot data parameter
# plot_channel = sensor_channels

# data selection 
'''plot_data_A or plot_data_B'''

print('Data selection process...')
for i in range(len(path_list)):
    plot_channel = sensor_channels
    df = pd.read_csv(path_list[i])
    df = remove_spike(df, channel=plot_channel[0], threshold=threshold)
    dict_set = auto_select(data=df)  
    all_select_range = {}    
    data_path = path_list[i]
    sensor_sn = sensor_list[i]
    a = select_data_7341(data_path, sensor_sn, plot_channel, MFC1_max_flow_rate, total_flow_rate,
                         cylinder_concentration, convert=spectrum_convert, remove_spike_switch=remove_spike_switch, 
                         threshold=threshold)
    
#     select range
#     selected_range_10 = {   
#              '10C 0ppm': (610, 10),
#              '10C 60ppm': (dict_set[1], 10),
#              '10C 25ppm': (dict_set[3], 10),
#              '10C 10ppm': (dict_set[5], 10),
#              '10C 4ppm': (dict_set[7], 10),
#               } 
    
#     selected_range_0 = { 
#              '0C 0ppm': (419, 10),
#              '0C 60ppm': (dict_set[9], 10),
#              '0C 25ppm': (dict_set[11], 10),
#              '0C 10ppm': (dict_set[13], 10),
#              '0C 4ppm': (dict_set[15], 10),                  
#               } 
    
#     selected_range_n10 = {   
#              'n10C 0ppm': (234, 10),
#              'n10C 60ppm': (dict_set[17], 10),
#              'n10C 25ppm': (dict_set[19], 10),
#              'n10C 10ppm': (dict_set[21], 10),
#              'n10C 4ppm': (dict_set[23], 10),                  
#               }
    
#     selected_range_n20 = {   
#              'n20C 0ppm': (46, 10),
#              'n20C 60ppm': (dict_set[25], 10),
#              'n20C 25ppm': (dict_set[27], 10),
#              'n20C 10ppm': (dict_set[29], 10),
#              'n20C 4ppm': (dict_set[31], 10),                  
#               }
    
#     selected_range_n10_blind_test = {
#              'n10Cb 0ppm': (3193, 10),
#              'n10Cb 60ppm': (dict_set[33], 10),
#              'n10Cb 25ppm': (dict_set[35], 10),
#              'n10Cb 10ppm': (dict_set[37], 10),
#              'n10Cb 4ppm': (dict_set[39], 10),                  
#              }

#     blind test dictionary
#     selected_range_n10_blind_test = {
#                  'n10Cb 0ppm': (dict_set[0], 10),
#                  'n10Cb 60ppm': (dict_set[1], 10),
#                  'n10Cb 25ppm': (dict_set[3], 10),
#                  'n10Cb 10ppm': (dict_set[5], 10),
#                  'n10Cb 4ppm': (dict_set[7], 10),                  
#                  }


# blind test dictionary
    selected_range_n10_blind_test = {
                 'n10Cb 0ppm': (dict_set[0], 10),
                 'n10Cb 60ppm': (dict_set[1], 10),
                 'n10Cb 25ppm': (dict_set[3], 10),
                 'n10Cb 10ppm': (dict_set[5], 10),
                 'n10Cb 4ppm': (dict_set[7], 10),                  
                 }
    
    
    
#     saveName = 'select_data_calibration_n20C'
#     select_range = selected_range_n20
#     all_select_range.update(select_range)
#     a.select_data_C(select_range, movingAverage=1)
#     a.plot_data_C(select_range) 
# #     a.plot_select_data()
#     a.save_data(saveName, select_range)

#     saveName = 'select_data_calibration_n10C'
#     select_range = selected_range_n10
#     all_select_range.update(select_range)
#     a.select_data_C(select_range, movingAverage=1)
#     a.plot_data_C(select_range) 
# #     a.plot_select_data()
#     a.save_data(saveName, select_range)
    
#     saveName = 'select_data_calibration_0C'
#     select_range = selected_range_0
#     all_select_range.update(select_range)
#     a.select_data_C(select_range, movingAverage=1)
#     a.plot_data_C(select_range) 
# #     a.plot_select_data()
#     a.save_data(saveName, select_range)
    
#     saveName = 'select_data_calibration_10C'
#     select_range = selected_range_10
#     all_select_range.update(select_range)    
#     a.select_data_C(select_range, movingAverage=1)
#     a.plot_data_C(select_range) 
# #     a.plot_select_data()
#     a.save_data(saveName, select_range)
    
#     saveName = 'select_data_calibration_20C'
#     select_range = selected_range_20
#     all_select_range.update(select_range)
#     a.select_data_C(select_range, movingAverage=1)
#     a.plot_data_C(select_range) 
#     a.plot_select_data()
#     a.save_data(saveName, select_range)
    
#     saveName = 'select_data_calibration_30C'
#     select_range = selected_range_30
#     all_select_range.update(select_range)
#     a.select_data_C(select_range, movingAverage=1)
#     a.plot_data_C(select_range) 
#     a.plot_select_data()
#     a.save_data(saveName, select_range)

#     saveName = 'select_data_calibration_35C'
#     select_range = selected_range_35
#     all_select_range.update(select_range)
#     a.select_data_C(select_range, movingAverage=1)
#     a.plot_data_C(select_range) 
#     a.plot_select_data()
#     a.save_data(saveName, select_range)
       
#     saveName = 'select_data_calibration_45C'
#     select_range = selected_range_45
#     all_select_range.update(select_range)
#     a.select_data_C(select_range, movingAverage=1)
#     a.plot_data_C(select_range) 
#     a.plot_select_data()
#     a.save_data(saveName, select_range)
    
#     saveName = 'select_data_blind_test_n20C'
#     select_range = selected_range_n20_blind_test
#     all_select_range.update(select_range)   
#     a.select_data_C(select_range, movingAverage=1)
#     a.plot_data_C(select_range) 
#     a.plot_select_data()
#     a.save_data(saveName, select_range)
    
    saveName = 'select_data_blind_test_n10C'
    select_range = selected_range_n10_blind_test
    all_select_range.update(select_range)   
    a.select_data_C(select_range, movingAverage=1)
    a.plot_data_C(select_range) 
#     a.plot_select_data()
    a.save_data(saveName, select_range)

#     saveName = 'select_data_blind_test_n10C'
#     select_range = selected_range_n10_blind_test
#     all_select_range.update(select_range)   
#     a.select_data_C(select_range, movingAverage=1)
#     a.plot_data_C(select_range) 
#     a.plot_select_data()
#     a.save_data(saveName, select_range)
    
#     saveName = 'select_data_blind_test_0C'
#     select_range = selected_range_40_blind_test
#     all_select_range.update(select_range)   
#     a.select_data_C(select_range, movingAverage=1)
#     a.plot_data_C(select_range) 
#     a.plot_select_data()
#     a.save_data(saveName, select_range)

#     saveName = 'select_data_blind_test_10C'
#     select_range = selected_range_10_blind_test
#     all_select_range.update(select_range)   
#     a.select_data_C(select_range, movingAverage=1)
#     a.plot_data_C(select_range) 
#     a.plot_select_data()
#     a.save_data(saveName, select_range)
    
#     saveName = 'select_data_blind_test_20C_2'
#     select_range = selected_range_20_blind_test
#     all_select_range.update(select_range)   
#     a.select_data_C(select_range, movingAverage=1)
#     a.plot_data_C(select_range) 
#     a.plot_select_data()
#     a.save_data(saveName, select_range)
    
#     saveName = 'select_data_blind_test_30C_2'
#     select_range = selected_range_30_blind_test
#     all_select_range.update(select_range)   
#     a.select_data_C(select_range, movingAverage=1)
#     a.plot_data_C(select_range) 
#     a.plot_select_data()
#     a.save_data(saveName, select_range)
    
#     saveName = 'select_data_blind_test_40C_2'
#     select_range = selected_range_40_blind_test
#     all_select_range.update(select_range)   
#     a.select_data_C(select_range, movingAverage=1)
#     a.plot_data_C(select_range) 
#     a.plot_select_data()
#     a.save_data(saveName, select_range)
    
    # save mapping figure
    plot_channel = sensor_channels[0]
    save_mapping_figure.save_mapping_figure(df, data_path, sensor_sn, plot_channel, all_select_range)
print('Data selection complete')

# # save mapping figure
# plot_channel = sensor_channels[0]
# save_mapping_figure.save_mapping_figure(df, data_path, sensor_sn, plot_channel, all_select_range)

Data selection process...
AMS1_spike_index Int64Index([], dtype='int64')
AMS2_spike_index Int64Index([], dtype='int64')
AMS1_spike_index Int64Index([], dtype='int64')
AMS2_spike_index Int64Index([], dtype='int64')
spectrum convert to CIE and Lab process ...
spectrum convert to CIE and Lab process complete
Select data shape: (50, 53)


#20200814093320 save mapping figure complete
AMS1_spike_index Int64Index([], dtype='int64')
AMS2_spike_index Int64Index([], dtype='int64')
AMS1_spike_index Int64Index([], dtype='int64')
AMS2_spike_index Int64Index([], dtype='int64')
spectrum convert to CIE and Lab process ...
spectrum convert to CIE and Lab process complete
Select data shape: (50, 53)


#20200814093632 save mapping figure complete
AMS1_spike_index Int64Index([], dtype='int64')
AMS2_spike_index Int64Index([], dtype='int64')
AMS1_spike_index Int64Index([], dtype='int64')
AMS2_spike_index Int64Index([], dtype='int64')
spectrum convert to CIE and Lab process ...
spectrum convert to CIE and Lab process complete
Select data shape: (50, 53)


#20200817093518 save mapping figure complete
AMS1_spike_index Int64Index([], dtype='int64')
AMS2_spike_index Int64Index([], dtype='int64')
AMS1_spike_index Int64Index([], dtype='int64')
AMS2_spike_index Int64Index([], dtype='int64')
spectrum convert to CIE and Lab process ...
spectrum convert to CIE and Lab process complete
Select data shape: (50, 53)


#20200819094714 save mapping figure complete
AMS1_spike_index Int64Index([], dtype='int64')
AMS2_spike_index Int64Index([], dtype='int64')
AMS1_spike_index Int64Index([], dtype='int64')
AMS2_spike_index Int64Index([], dtype='int64')
spectrum convert to CIE and Lab process ...
spectrum convert to CIE and Lab process complete
Select data shape: (50, 53)


#20200915135041 save mapping figure complete
AMS1_spike_index Int64Index([], dtype='int64')
AMS2_spike_index Int64Index([], dtype='int64')
AMS1_spike_index Int64Index([], dtype='int64')
AMS2_spike_index Int64Index([], dtype='int64')
spectrum convert to CIE and Lab process ...
spectrum convert to CIE and Lab process complete
Select data shape: (50, 53)


#20200917104028 save mapping figure complete
AMS1_spike_index Int64Index([], dtype='int64')
AMS2_spike_index Int64Index([], dtype='int64')
AMS1_spike_index Int64Index([], dtype='int64')
AMS2_spike_index Int64Index([], dtype='int64')
spectrum convert to CIE and Lab process ...
spectrum convert to CIE and Lab process complete
Select data shape: (50, 53)


#20200917104408 save mapping figure complete
AMS1_spike_index Int64Index([], dtype='int64')
AMS2_spike_index Int64Index([], dtype='int64')
AMS1_spike_index Int64Index([], dtype='int64')
AMS2_spike_index Int64Index([], dtype='int64')
spectrum convert to CIE and Lab process ...
spectrum convert to CIE and Lab process complete
Select data shape: (50, 53)


#20200918095055 save mapping figure complete
Data selection complete
